# Extracción de datos

Datos extraídos desde la API de [Datos Abiertos
Legislativos](https://opendata.camara.cl).

In [ ]:
import xml.etree.ElementTree as ET
import requests
from time import sleep

import pandas as pd
from datetime import datetime

In [ ]:
# fechas para las cuales se tomará información
start_date = datetime.strptime("2022-03-11", "%Y-%m-%d")
end_date = datetime.strptime("2025-07-24", "%Y-%m-%d")

# prefijo para los sitios de las requests
vote_req_prefix = "https://opendata.camara.cl/camaradiputados/WServices/WSLegislativo.asmx/"
deputy_req_prefix = "https://opendata.camara.cl/camaradiputados/WServices/WSDiputado.asmx/"

# prefijo para las tags de los archivos XML
tag_prefix = r"{http://opendata.camara.cl/camaradiputados/v1}"


# función auxiliar para parsear fechas
def parse_date(date_str):
   return datetime.strptime(date_str, "%Y-%m-%dT%H:%M:%S")

## Votaciones

Para cada año de nuestro interés, se obtienen todas las votaciones de ese año.
Para cada votación de interés dentro del año, buscamos y guardamos la opción
por la cual votó cada uno de los diputados.

In [ ]:
votes_dict = {}  # diccionario con todas las votaciones

# en orden inverso (porque así está ordenado el XML)
years = range(end_date.year, start_date.year-1, -1)

for year in years:

    # obtenemos lista de votaciones de ese año
    votings_request = requests.get(
        vote_req_prefix + "retornarVotacionesXAnno",
        params={"prmAnno": year}
    )
    votings = ET.fromstring(votings_request.content)

    for voting in votings:
        
        # revisa si la votación está dentro de los límites, la salta si no
        voting_date_text = voting.find(tag_prefix + "Fecha").text
        voting_date = parse_date(voting_date_text)
        if voting_date < start_date or voting_date > end_date:
            continue
        
        voting_id = voting.find(tag_prefix + "Id").text
        print(
            f"Procesando votación {voting_id} ({voting_date_text})", end="\r"
        )
        
        # obtenemos detalles de la votación
        while True:
            try:
                voting_detail_request = requests.get(
                    vote_req_prefix + "retornarVotacionDetalle",
                    params={"prmVotacionId": voting_id}
                )
                voting_detail = ET.fromstring(voting_detail_request.content)
                break
            except:
                print(f"Votación {voting_id} falló, reintentando..." + " "*20)
                sleep(10)
        
        # votos individuales en la votación
        votes = voting_detail.find(tag_prefix + "Votos")
        
        if votes is not None:
            votes_dict[voting_id] = {}  # dict de la votación actual
            for vote in votes:
                
                deputy_id = (
                    vote
                    .find(tag_prefix + "Diputado")
                    .find(tag_prefix + "Id")
                    .text
                )
                deputy_choice = vote.find(
                    tag_prefix + "OpcionVoto"
                ).attrib["Valor"]
                
                # se agrega al diccionario
                votes_dict[voting_id][deputy_id] = deputy_choice

Votación 83483 falló, reintentando...                    
Votación 81803 falló, reintentando...                    


In [31]:
vote_df = pd.DataFrame(votes_dict)
vote_df = vote_df.astype(float)

vote_df

83902  83901  83900  83899  83898  83897  83896  83886  83885  83884  \
1185    1.0    1.0    1.0    1.0    4.0    4.0    4.0    0.0    1.0    1.0   
1096    4.0    4.0    4.0    4.0    1.0    0.0    0.0    4.0    0.0    1.0   
1097    1.0    1.0    1.0    1.0    1.0    0.0    0.0    4.0    1.0    1.0   
1098    1.0    4.0    4.0    4.0    4.0    2.0    4.0    1.0    0.0    1.0   
1009    1.0    1.0    0.0    0.0    4.0    4.0    4.0    4.0    1.0    4.0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
1086    1.0    1.0    1.0    1.0    1.0    4.0    4.0    1.0    1.0    1.0   
1087    1.0    1.0    1.0    1.0    1.0    0.0    4.0    4.0    1.0    1.0   
1184    1.0    1.0    1.0    1.0    1.0    0.0    0.0    1.0    0.0    1.0   
1124    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1115    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   

      ...  23434  23433  27756  27755  27754  27753  27752  38500  38499  \
1185  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1096  ...    0.0    1.0    1.0    1.0    1.0    1.0    1.0    0.0    0.0   
1097  ...    2.0    1.0    1.0    1.0    1.0    1.0    1.0    1.0    2.0   
1098  ...    1.0    1.0    1.0    1.0    1.0    1.0    1.0    1.0    1.0   
1009  ...    1.0    1.0    1.0    1.0    1.0    1.0    0.0    1.0    1.0   
...   ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
1086  ...    0.0    1.0    1.0    1.0    1.0    1.0    1.0    1.0    0.0   
1087  ...    0.0    1.0    1.0    1.0    1.0    1.0    1.0    1.0    0.0   
1184  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1124  ...    0.0    1.0    1.0    1.0    1.0    1.0    1.0    1.0    0.0   
1115  ...    0.0    1.0    1.0    1.0    1.0    1.0    1.0    1.0    0.0   

      38498  
1185    NaN  
1096    0.0  
1097    2.0  
1098    1.0  
1009    1.0  
...     ...  
1086    0.0  
1087    0.0  
1184    NaN  
1124    0.0  
1115    0.0  

[157 rows x 5597 columns]

In [32]:
vote_df.to_csv("data/votos.csv")

## Diputados

Se guarda la información de todos los diputados (luego se filtrarán solo los
que aparecen en las votaciones).

In [26]:
deputy_indices = []
deputy_data = []

deputies_request = requests.get(deputy_req_prefix + "retornarDiputados")
deputies = ET.fromstring(deputies_request.content)

for deputy in deputies:
    
    deputy_id = deputy.find(tag_prefix + "Id").text
    
    # caso borde
    if deputy_id == "9999":
        continue
    
    deputy_first_name = deputy.find(tag_prefix + "Nombre").text
    deputy_last_name = deputy.find(tag_prefix + "ApellidoPaterno").text
    deputy_sex = deputy.find(tag_prefix + "Sexo").text

    # último partido al cual ha pertenecido el diputado
    militancies = deputy.find(tag_prefix + "Militancias")
    last_militancy_start = None
    deputy_party = None
    for militancy in militancies:
        
        militancy_start_text = militancy.find(tag_prefix + "FechaInicio").text
        militancy_start = parse_date(militancy_start_text)
        if (
            militancy_start < end_date and
            (
                last_militancy_start is None
                or militancy_start > last_militancy_start
            )
        ):
            last_militancy_start = militancy_start
            deputy_party = (
                militancy
                .find(tag_prefix + "Partido")
                .find(tag_prefix + "Nombre")
                .text
            )
    
    deputy_indices.append(deputy_id)
    deputy_data.append([
        deputy_first_name,
        deputy_last_name,
        deputy_sex,
        deputy_party
    ])
    

In [27]:
deputy_df = pd.DataFrame(
    index=deputy_indices,
    columns=["nombre", "apellido", "sexo", "partido"],
    data=deputy_data
)
deputy_df

nombre   apellido       sexo                        partido
208         Víctor      Pérez  Masculino  Unión Demócrata Independiente
485          Jorge    Pizarro  Masculino    Partido Demócrata Cristiano
684         Sergio    Pizarro  Masculino    Partido Demócrata Cristiano
696   José Alfonso  Rodríguez  Masculino            Renovación Nacional
951          David   Sandoval  Masculino  Unión Demócrata Independiente
...            ...        ...        ...                            ...
1135      Johannes     Kaiser  Masculino    Partido Nacional Libertario
1144     Christian   Matheson  Masculino                 Independientes
1149         Carla    Morales   Femenino            Renovación Nacional
1185        Arturo    Barrios  Masculino             Partido Socialista
1184       Roberto    Celedón  Masculino                 Independientes

[553 rows x 4 columns]

In [30]:
deputy_df.to_csv("data/diputados.csv")